In [13]:
import numpy as np
import pandas as pd
import pycbc.psd
from pycbc import frame
from astropy.time import Time
import h5py
from pycbc.filter import sigma,sigmasq
from pycbc.waveform.generator import FDomainCBCGenerator,FDomainDetFrameGenerator
from tqdm import tqdm
import healpy as hp

import matplotlib as mpl
import matplotlib.pyplot as plt

# PLOTTING OPTIONS
fig_width_pt = 3*246.0  # Get this from LaTeX using \showthe\columnwidth
inches_per_pt = 1.0/72.27               # Convert pt to inch
golden_mean = (np.sqrt(5)-1.0)/2.0         # Aesthetic ratio
fig_width = fig_width_pt*inches_per_pt  # width in inches
fig_height = fig_width*golden_mean      # height in inches
fig_size =  [fig_width,fig_height]

params = { 'axes.labelsize': 24,
          'font.family': 'serif',
          'font.serif': 'Computer Modern Raman',
          'font.size': 24,
          'legend.fontsize': 20,
          'xtick.labelsize': 24,
          'ytick.labelsize': 24,
          'axes.grid' : True,
          'text.usetex': True,
          'savefig.dpi' : 100,
          'lines.markersize' : 14,
          'figure.figsize': fig_size}

mpl.rcParams.update(params)

In [14]:
from pycbc.inference import io

In [15]:
from pycbc import cosmology

In [16]:
gwname= []
grbname = []
gwtime = []
grbtime = []
gwstat = []
rankstat = []
far = []

m1=[]
m2=[]
d50 = []
d5=[]
d95=[]

for o in ['o1','o2','o3a','o3b']:
    search_result = pd.read_csv(
        '/work/yifan.wang/grb/git-notebooks/search_result_'+o+'.csv')
    for i in range(len(search_result.index)):
        gwtime.append(search_result['gwtime'][i])
        gwname.append(search_result['gwname'][i])
        grbname.append(search_result['grbname'][i])
        grbtime.append(search_result['grbtime'][i])
        gwstat.append(search_result['gwstat'][i])
        rankstat.append(search_result['rank_stat'][i])
        far.append(search_result['false_alarm_rate'][i])
        
        result = io.loadfile(
        '/work/yifan.wang/grb/gwrun/'+o+'/result/'+search_result['gwname'][i]+'.hdf','r')
        c = result.read_samples(['comoving_volume'])
        d = cosmology.distance_from_comoving_volume(c['comoving_volume'])
        d5 = np.quantile(d,0.05)
        d50.append(np.quantile(d,0.5))
        d95.append(np.quantile(d,0.95))
        
        config = result.read_config_file()
        m1.append(config.get('trigger','mass1'))
        m2.append(config.get('trigger','mass2'))

In [17]:
result_dict = {
            'gwname': gwname,
            'gwtime': gwtime,
            'gwstat': gwstat,
            'grbname': grbname,
            'grbtime': grbtime,
            'gwmass1': m1,
            'gwmass2': m2,
            'gwdistance5':d5,
            'gwdistance50':d50,
            'gwdistance95':d95,
            'rankstat':rankstat,
            'false_alarm_rate':far
          }
df= pd.DataFrame(result_dict)
df.to_csv('print_mass.csv',index=False)

In [18]:
df

gwname                         gwtime    gwstat       grbname  \
0   151001_082025  2015-10-01 08:20:25.612304688  3.216300  GRB151001348   
1   151029_074936  2015-10-29 07:49:36.257080078  4.217384    GRB151029A   
2   151027_224040  2015-10-27 22:40:40.125732422  7.388242    GRB151027B   
3   170330_222948  2017-03-30 22:29:48.292968750  6.867164    GRB170330A   
4   170723_161524  2017-07-23 16:15:24.278564453  1.803131  GRB170723677   
5   170409_024157  2017-04-09 02:41:57.491943359  1.875275  GRB170409112   
6   170402_065048  2017-04-02 06:50:48.413818359  1.078557  GRB170402285   
7   170424_101224  2017-04-24 10:12:24.813476563  1.744711  GRB170424425   
8   170626_093721  2017-06-26 09:37:21.972900391  0.376057    GRB170626A   
9   170825_120003  2017-08-25 12:00:03.797363281  0.244853  GRB170825500   
10  170323_012316  2017-03-23 01:23:16.403076172  4.556538  GRB170323058   
11  170629_125329  2017-06-29 12:53:29.332763672  3.580701    GRB170629A   
12  190404_070114  2019-04-04 07:01:14.184570313  1.717899  GRB190404293   
13  190701_094513  2019-07-01 09:45:13.635498047  3.444505    GRB190701A   
14  190613_040717  2019-06-13 04:07:17.935302734  1.669169    GRB190613A   
15  190827_111245  2019-08-27 11:12:45.835693359  1.306569  GRB190827467   
16  190508_234118  2019-05-08 23:41:18.096435547  0.587935  GRB190508987   
17  190628_123052  2019-06-28 12:30:52.782470703  0.360443  GRB190628521   
18  190726_152445  2019-07-26 15:24:45.007812500  0.653950  GRB190726642   
19  190623_110326  2019-06-23 11:03:26.475097656  0.667043  GRB190623461   
20  190919_181958  2019-09-19 18:19:58.394287109  0.726322  GRB190919764   
21  190805_044554  2019-08-05 04:45:54.454589844  3.164267  GRB190805199   
22  190422_160459  2019-04-22 16:04:59.637695313  4.248449  GRB190422670   
23  190824_144634  2019-08-24 14:46:34.029785156  0.774209    GRB190824A   
24  200205_201716  2020-02-05 20:17:16.676025391  4.175298  GRB200205845   
25  191213_060532  2019-12-13 06:05:32.067871094  4.082384  GRB191213254   
26  191110_140525  2019-11-10 14:05:25.402832031  0.338772  GRB191110587   
27  191213_040623  2019-12-13 04:06:23.358642578  2.728866    GRB191213A   
28  200216_090724  2020-02-16 09:07:24.385253906  0.623394  GRB200216380   
29  191119_061605  2019-11-19 06:16:05.898925781  5.132669  GRB191119261   
30  200317_004025  2020-03-17 00:40:25.055419922  0.621945  GRB200317028   
31  200117_122400  2020-01-17 12:24:00.887939453  2.896282  GRB200117517   

                          grbtime   gwmass1   gwmass2  gwdistance5  \
0   2015-10-01 08:20:35.168999910  1.250589  1.334340   169.553615   
1   2015-10-29 07:49:38.965140104  1.989062  1.309817   169.553615   
2   2015-10-27 22:40:40.667479992  2.076629  2.304049   169.553615   
3   2017-03-30 22:29:51.341320038  1.134269  1.276391   169.553615   
4   2017-07-23 16:15:27.855000019  1.201192  1.026384   169.553615   
5   2017-04-09 02:42:00.490000010  1.005010  1.018541   169.553615   
6   2017-04-02 06:50:54.391000032  1.171782  7.705198   169.553615   
7   2017-04-24 10:12:30.753999949  1.005258  1.390025   169.553615   
8   2017-06-26 09:37:23.124540091  1.045140  1.759012   169.553615   
9   2017-08-25 12:00:05.997999907  1.022295  1.652022   169.553615   
10  2017-03-23 01:23:23.269000053  1.408000  4.098881   169.553615   
11  2017-06-29 12:53:33.156640053  2.430000  2.550380   169.553615   
12  2019-04-04 07:01:21.924999952  1.292941  1.085623   169.553615   
13  2019-07-01 09:45:20.833659887  1.258383  1.116728   169.553615   
14  2019-06-13 04:07:18.310159922  1.088041  1.726374   169.553615   
15  2019-08-27 11:12:48.546000004  1.846564  1.764380   169.553615   
16  2019-05-08 23:41:24.148000002  1.359403  1.490797   169.553615   
17  2019-06-28 12:30:55.319999933  1.723257  1.849744   169.553615   
18  2019-07-26 15:24:53.609999895  1.008762  1.000003   169.553615   
19  2019-06-23 11:03:27.095000029  1.718099  1.637231   169.553615   
20  2019-09-19 18:20:02.65599989